In [44]:
import pandas as pd
import numpy as np
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColumnDataSource, HoverTool, Tabs, TabPanel, Legend,  Toggle, LegendItem, CustomJS, Select, Button
from bokeh.palettes import Category20
from bokeh.layouts import column
import os

# LinkedIn Women’s Representation 

## Share of women evolution

In [45]:
gender_file = '../../data/LinkedIn/Gender Sept 2025.xlsx'
gender_country = pd.read_excel(gender_file, sheet_name='1- Women by Ctry Yr')
gender_flow = pd.read_excel(gender_file, sheet_name='2 - Women by Ctry Ind Yr')
women_stem = pd.read_excel(gender_file, sheet_name='5 - Women by Ctry, STEM Occ')


In [46]:
import pandas as pd

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, HoverTool, Panel, Tabs, Legend, Div
from bokeh.palettes import Category10
from bokeh.layouts import column

output_notebook()

# ---------------------------------
# 1. Data prep
# ---------------------------------
df = gender_country.copy()

df["year_start_employed"] = df["year_start_employed"].astype(int)
df["women_pct"] = df["women_perc"] * 100  # convert to percentage


# ---------------------------------
# 2. Define peer groups
# ---------------------------------
peer_groups = {
    "MENA (regional peers)": [
        "Algeria", "Egypt", "Iraq", "Jordan", "Morocco", "Tunisia"
    ],
    "Non-MENA (structural peers)": [
        "Algeria", "Uzbekistan", "Ecuador", "Peru", "Ghana", "Vietnam", "Colombia"
    ],
    "Non-MENA (aspirational peers)": [
        "Algeria", "Chile", "Kazakhstan", "Malaysia", "Poland", "Romania", "Turkey"
    ]
}

tabs = []

# ---------------------------------
# 3. One figure per peer group
# ---------------------------------
for group_name, countries in peer_groups.items():
    sub = df[df["country_name"].isin(countries)].copy()
    if sub.empty:
        continue

    sub = sub.sort_values(["country_name", "year_start_employed"])

    max_pct = sub["women_pct"].max()
    y_max = min(100, max_pct * 1.15)

    unique_countries = sub["country_name"].unique().tolist()
    colors = Category10[max(3, min(10, len(unique_countries)))]

    p = figure(
        height=430,
        width=780,
        title=f"Share of women in employment over time – {group_name}",
        toolbar_location=None
    )

    legend_items = []
    point_renderers = []

    for i, c in enumerate(unique_countries):
        dc = sub[sub["country_name"] == c]
        src = ColumnDataSource(dc)
        color = colors[i % len(colors)]

        line_r = p.line(
            x="year_start_employed",
            y="women_pct",
            source=src,
            line_width=3,
            color=color,
            muted_alpha=0.15
        )
        scat_r = p.scatter(
            x="year_start_employed",
            y="women_pct",
            source=src,
            size=7,
            color=color
        )

        legend_items.append((c, [line_r, scat_r]))
        point_renderers.append(scat_r)

    p.add_tools(HoverTool(
        renderers=point_renderers,
        tooltips=[
            ("Year", "@year_start_employed"),
            ("% women", "@women_pct{0.0}%")
        ],
        mode="mouse"
    ))

    p.xaxis.axis_label = "Year"
    p.yaxis.axis_label = "Women as % of employed"
    p.y_range.start = 0
    p.y_range.end = y_max
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_alpha = 0.15

    legend = Legend(
        items=legend_items,
        location="center",
        orientation="horizontal",
        padding=2,
        spacing=3,
        glyph_width=10,
        glyph_height=10,
        label_text_font_size="9pt",
    )
    legend.ncols = min(5, len(unique_countries))
    legend.click_policy = "mute"
    p.add_layout(legend, "below")

    tabs.append(TabPanel(child=p, title=group_name))


# ---------------------------------
# 4. Add GLOBAL TITLE here
# ---------------------------------
title_div = Div(
    text="""
    <h2 style='text-align:center; margin:0; font-size:20px;'>
    Women as a Share of Employed LinkedIn Members, by Country and Year (2015–2025)
    </h2>
    """,
    width=800
)

layout = column(title_div, Tabs(tabs=tabs))

show(layout)



Loading BokehJS ...

In [47]:
import pandas as pd

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, HoverTool, Panel, Tabs, Legend
from bokeh.palettes import Category10

output_notebook()

peer_countries = ["Algeria", "Egypt", "Iraq", "Jordan", "Morocco", "Tunisia"]

df = gender_flow.copy()
df = df[df["country_name"].isin(peer_countries)].copy()
df["year_start_employed"] = df["year_start_employed"].astype(int)
df["women_pct"] = df["women_perc"] * 100

tabs = []

for country in peer_countries:
    sub = df[df["country_name"] == country].copy()
    if sub.empty:
        continue

    industries = sub["Industry"].unique().tolist()
    colors = Category10[max(3, min(10, len(industries)))]

    p = figure(
        height=430,  # a bit larger so plot area dominates
        width=780,
        title=f"Share of women in employment over time – {country}",
        toolbar_location=None
    )

    scatter_renderers = []
    legend_items = []

    for i, ind in enumerate(industries):
        di = sub[sub["Industry"] == ind].sort_values("year_start_employed")
        src = ColumnDataSource(di)
        color = colors[i % len(colors)]

        line_r = p.line(
            x="year_start_employed",
            y="women_pct",
            source=src,
            line_width=3,
            color=color,
            muted_alpha=0.15
        )
        scat_r = p.scatter(
            x="year_start_employed",
            y="women_pct",
            source=src,
            size=6,
            color=color
        )

        scatter_renderers.append(scat_r)
        legend_items.append((ind, [line_r, scat_r]))

    # Tooltip only for points
    p.add_tools(HoverTool(
        tooltips=[
            ("Year", "@year_start_employed"),
            ("% women", "@women_pct{0.0}%")
        ],
        renderers=scatter_renderers,
        mode="mouse"
    ))

    p.xaxis.axis_label = "Year"
    p.yaxis.axis_label = "Women as % of employed"
    p.y_range.start = 0
    p.y_range.end = 50
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_alpha = 0.15

    # ----------------------------------------
    #     SUPER COMPACT LEGEND BELOW PLOT
    # ----------------------------------------
    legend = Legend(
        items=legend_items,
        location="center",
        orientation="horizontal",
        padding=2,
        spacing=3,
        glyph_width=10,
        glyph_height=10,
        label_text_font_size="7.5pt",   # smaller labels
    )

    # Put legend below
    p.add_layout(legend, "below")

    # More columns → fewer rows → more compact
    legend.ncols = min(4, len(industries))  # up to 5 per row

    # Interactivity
    legend.click_policy = "mute"

    tabs.append(TabPanel(child=p, title=country))

show(Tabs(tabs=tabs))





Loading BokehJS ...

In [48]:
import pandas as pd

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, HoverTool, Panel, Tabs, Legend, Div
from bokeh.palettes import Category10
from bokeh.layouts import column

output_notebook()

# ---------------------------------
# 1. Data prep  (STEM)
# ---------------------------------
df = women_stem.copy()   # <– STEM data

# columns: year_start_employed | country_name | women_perc
df["year_start_employed"] = df["year_start_employed"].astype(int)
df["women_pct"] = df["women_perc"] * 100  # 0–1 → %

# ---------------------------------
# 2. Peer groups (same as before)
# ---------------------------------
peer_groups = {
    "MENA (regional peers)": [
        "Algeria", "Egypt", "Iraq", "Jordan", "Morocco", "Tunisia"
    ],
    "Non-MENA (structural peers)": [
        "Algeria", "Uzbekistan", "Ecuador", "Peru", "Ghana", "Vietnam", "Colombia"
    ],
    "Non-MENA (aspirational peers)": [
        "Algeria", "Chile", "Kazakhstan", "Malaysia", "Poland", "Romania", "Turkey"
    ]
}

tabs = []

# ---------------------------------
# 3. One figure per peer group
# ---------------------------------
for group_name, countries in peer_groups.items():
    sub = df[df["country_name"].isin(countries)].copy()
    if sub.empty:
        continue

    sub = sub.sort_values(["country_name", "year_start_employed"])

    max_pct = sub["women_pct"].max()
    y_max = min(100, max_pct * 1.15)

    unique_countries = sub["country_name"].unique().tolist()
    colors = Category10[max(3, min(10, len(unique_countries)))]

    p = figure(
        height=430,
        width=780,
        title=f"Women in STEM occupations over time – {group_name}",
        toolbar_location=None
    )

    legend_items = []
    point_renderers = []

    for i, c in enumerate(unique_countries):
        dc = sub[sub["country_name"] == c]
        src = ColumnDataSource(dc)
        color = colors[i % len(colors)]

        line_r = p.line(
            x="year_start_employed",
            y="women_pct",
            source=src,
            line_width=3,
            color=color,
            muted_alpha=0.15
        )
        scat_r = p.scatter(
            x="year_start_employed",
            y="women_pct",
            source=src,
            size=7,
            color=color
        )

        legend_items.append((c, [line_r, scat_r]))
        point_renderers.append(scat_r)

    p.add_tools(HoverTool(
        renderers=point_renderers,
        tooltips=[
            ("Year", "@year_start_employed"),
            ("% women", "@women_pct{0.0}%")
        ],
        mode="mouse"
    ))

    p.xaxis.axis_label = "Year"
    p.yaxis.axis_label = "Women in STEM as % of employed"
    p.y_range.start = 0
    p.y_range.end = y_max
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_alpha = 0.15

    legend = Legend(
        items=legend_items,
        location="center",
        orientation="horizontal",
        padding=2,
        spacing=3,
        glyph_width=10,
        glyph_height=10,
        label_text_font_size="9pt",
    )
    legend.ncols = min(5, len(unique_countries))
    legend.click_policy = "mute"
    p.add_layout(legend, "below")

    tabs.append(TabPanel(child=p, title=group_name))

# ---------------------------------
# 4. Global title for STEM
# ---------------------------------
title_div = Div(
    text="""
    <h2 style='text-align:center; margin:0; font-size:20px;'>
    Women as a Share of Employed LinkedIn Members in STEM Occupations, 
    by Country and Year (2015–2024)
    </h2>
    """,
    width=800
)

layout = column(title_div, Tabs(tabs=tabs))
show(layout)


Loading BokehJS ...

## LinkedIn Women’s Representation Across Leadership Levels

In [49]:
# read excel skipping first rows, sheet = India Seniority Ind
df_gender = pd.read_excel(gender_file, sheet_name='India Seniority Ind', skiprows=2)

gender_industry_full = "../../data/LinkedIn/Gender Share Wkfc MENA by IND and SEN 2025 TO SHARE.xlsx"
gender_industry = pd.read_excel(gender_industry_full, sheet_name='Share of Women by IND, SEN, CTR', skiprows=1)

In [50]:
import pandas as pd

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import (
    ColumnDataSource, LinearColorMapper, ColorBar, BasicTicker,
    PrintfTickFormatter, LabelSet, Div
)
from bokeh.layouts import column
from bokeh.transform import transform
from bokeh.palettes import Blues256

output_notebook()

# -----------------------------
# 1. Original detailed columns
# -----------------------------
entry_cols = [
    '110.Entry-Level',
    '120.Experienced',
    '130.Distinguished'
]

mid_cols = [
    '200.Entry-Level Manager',
    '210.Experienced Manager',
    '220.Director-Level'
]

lead_cols_all = [
    '300.Vice President-Level',
    '310.CXO-Level',
    '320.Organizational Governance'
]
# Keep only leadership cols that actually exist in your df
lead_cols = [c for c in lead_cols_all if c in gender_industry.columns]

# -----------------------------
# 2. Filter to Algeria
# -----------------------------
dz = gender_industry[gender_industry['Country'] == 'Algeria'].copy()

# Make sure all source columns are numeric
dz[entry_cols + mid_cols + lead_cols] = dz[entry_cols + mid_cols + lead_cols].apply(
    pd.to_numeric, errors='coerce'
)

# -----------------------------
# 3. Build grouped averages
# -----------------------------
dz_agg = pd.DataFrame()
dz_agg['Industry'] = dz['Industry']

dz_agg['Entry-level'] = dz[entry_cols].mean(axis=1, skipna=True)
dz_agg['Mid-level management'] = dz[mid_cols].mean(axis=1, skipna=True)
dz_agg['Leadership'] = dz[lead_cols].mean(axis=1, skipna=True)

# -----------------------------
# 4. Long format for heatmap
# -----------------------------
df_long = dz_agg.melt(
    id_vars='Industry',
    value_vars=['Entry-level', 'Mid-level management', 'Leadership'],
    var_name='Level',
    value_name='Women_share'
)

# Force numeric
df_long['Women_share'] = pd.to_numeric(df_long['Women_share'], errors='coerce')

# ---- NEW: work in percentages (0–100) for colors & bar ----
df_long['Women_share_pct'] = df_long['Women_share'] * 100

# Percent label (for the text in the cells)
df_long['pct_label'] = df_long['Women_share_pct'].round(0).astype('Int64').astype(str) + "%"

# Sort industries by entry-level share (descending)
order = (
    dz_agg.sort_values('Entry-level', ascending=False)['Industry']
          .tolist()
)
df_long['Industry'] = pd.Categorical(df_long['Industry'], categories=order, ordered=True)

levels = ['Entry-level', 'Mid-level management', 'Leadership']
industries = list(reversed(order))

source = ColumnDataSource(df_long)

# -----------------------------
# 5. Heatmap (table-style)
# -----------------------------
# ---- NEW: palette starting at pure white, and low=0 ----
palette = list(reversed(Blues256))

color_mapper = LinearColorMapper(
    palette=palette,
    low=0,
    high=df_long['Women_share_pct'].max()
)

p = figure(
    x_range=levels,
    y_range=industries,
    height=500,
    width=750,
    toolbar_location=None,
    title="Percentage of women by level – Algeria"
)

p.rect(
    x="Level",
    y="Industry",
    width=1,
    height=1,
    source=source,
    line_color=None,
    # ---- map using the % column ----
    fill_color=transform('Women_share_pct', color_mapper)
)

labels = LabelSet(
    x='Level',
    y='Industry',
    text='pct_label',
    source=source,
    text_align='center',
    text_baseline='middle',
    text_color='white'
)
p.add_layout(labels)

# ---- Color bar now also uses 0–100 and prints nicely ----
color_bar = ColorBar(
    color_mapper=color_mapper,
    ticker=BasicTicker(desired_num_ticks=5),
    formatter=PrintfTickFormatter(format="%.0f%%"),
    label_standoff=8,
    location=(0, 0),
    orientation='horizontal'
)
p.add_layout(color_bar, 'below')

p.xaxis.axis_label = "Position level"
p.yaxis.axis_label = ""

p.axis.major_tick_line_color = None
p.axis.minor_tick_line_color = None
p.grid.grid_line_color = None

title_div = Div(
    text="<h2 style='text-align:center; margin-bottom:10px;'>Women’s Representation Across Leadership Levels by Industry – Algeria</h2>"
)

layout = column(title_div, p)
show(layout)


Loading BokehJS ...

In [51]:
import pandas as pd

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, LabelSet, Div
from bokeh.layouts import column
from bokeh.palettes import Blues9, Oranges9, Greens9

output_notebook()

# -----------------------------
# 1. Level categories & palettes
# -----------------------------
LEVELS = ["Entry-level", "Mid-level management", "Leadership"]

palette_map = {
    "Entry-level": list(reversed(Blues9)),              # light → dark blue
    "Mid-level management": list(reversed(Oranges9)),   # light → dark orange
    "Leadership": list(reversed(Greens9))               # light → dark green
}

# -----------------------------
# 2. Filter to Algeria & build averages
# -----------------------------
entry_cols = [
    '110.Entry-Level',
    '120.Experienced',
    '130.Distinguished'
]

mid_cols = [
    '200.Entry-Level Manager',
    '210.Experienced Manager',
    '220.Director-Level'
]

lead_cols_all = [
    '300.Vice President-Level',
    '310.CXO-Level'

]
lead_cols = [c for c in lead_cols_all if c in gender_industry.columns]

dz = gender_industry[gender_industry['Country'] == 'Algeria'].copy()

dz[entry_cols + mid_cols + lead_cols] = dz[entry_cols + mid_cols + lead_cols].apply(
    pd.to_numeric, errors='coerce'
)

dz_agg = pd.DataFrame()
dz_agg["Industry"] = dz["Industry"]
dz_agg["Entry-level"] = dz[entry_cols].mean(axis=1, skipna=True)
dz_agg["Mid-level management"] = dz[mid_cols].mean(axis=1, skipna=True)
dz_agg["Leadership"] = dz[lead_cols].mean(axis=1, skipna=True)

# -----------------------------
# 3. Long format
# -----------------------------
df_long = dz_agg.melt(
    id_vars="Industry",
    value_vars=LEVELS,
    var_name="Level",
    value_name="Women_share"
)

df_long["Women_share_pct"] = df_long["Women_share"] * 100
df_long["pct_label"] = (
    df_long["Women_share_pct"]
    .round(0)
    .astype("Int64")
    .astype(str)
    + "%"
)

# Order industries by Entry-level (descending)
order = (
    dz_agg.sort_values("Entry-level", ascending=False)["Industry"]
          .tolist()
)
df_long["Industry"] = pd.Categorical(
    df_long["Industry"],
    categories=order,
    ordered=True
)

# -----------------------------
# 4. Column-wise color scaling
# -----------------------------
def map_to_palette(values, palette):
    """Map a numeric series to a list of hex colors using full palette range."""
    vals = values.astype(float)
    vmin, vmax = vals.min(), vals.max()
    if pd.isna(vmin) or pd.isna(vmax) or vmin == vmax:
        # all same or all NaN → use middle color
        mid_color = palette[len(palette) // 2]
        return [mid_color] * len(vals)

    n = len(palette)
    colors = []
    for v in vals:
        if pd.isna(v):
            colors.append("#ffffff")
        else:
            t = (v - vmin) / (vmax - vmin)  # 0..1
            idx = int(round(t * (n - 1)))
            idx = max(0, min(n - 1, idx))
            colors.append(palette[idx])
    return colors

# compute colors per level
df_long["color"] = "#ffffff"  # default

for lvl in LEVELS:
    mask = df_long["Level"] == lvl
    vals = df_long.loc[mask, "Women_share_pct"]
    pal = palette_map[lvl]
    df_long.loc[mask, "color"] = map_to_palette(vals, pal)

source = ColumnDataSource(df_long)

# -----------------------------
# 5. Plot
# -----------------------------
p = figure(
    x_range=LEVELS,
    y_range=list(reversed(order)),
    height=500,
    width=750,
    toolbar_location=None,
    title="Percentage of women by level – Algeria"
)

p.rect(
    x="Level",
    y="Industry",
    width=1,
    height=1,
    source=source,
    line_color=None,
    fill_color="color"
)

labels = LabelSet(
    x='Level',
    y='Industry',
    text='pct_label',
    source=source,
    text_align='center',
    text_baseline='middle',
    text_color='white'
)
p.add_layout(labels)

p.xaxis.axis_label = "Position level"
p.yaxis.axis_label = ""

p.axis.major_tick_line_color = None
p.axis.minor_tick_line_color = None
p.grid.grid_line_color = None

title_div = Div(
    text="<h2 style='text-align:center; margin-bottom:10px;'>Women’s Representation Across Leadership Levels by Industry – Algeria</h2>"
)

layout = column(title_div, p)
show(layout)




Loading BokehJS ...

- **Women are better represented at entry-level across nearly all industries**, typically ranging from 20–40%.  
  Industries such as *Hospitals and Health Care*, *Education*, and *Financial Services* show the highest female participation at the early career stage.

- **Decline occurs as seniority increases.**  
  Mid-level management tends to show a substantial drop in representation, and the decline continues into leadership roles. 

- **A few sectors show slightly better retention of women into leadership**, including *hospitals and Health Care*, *Retail*, *Accommodation and Food Services*, and *Government*, though the overall representation still remains low.


In [52]:
import pandas as pd

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, HoverTool, Panel, Tabs
from bokeh.layouts import column
from bokeh.palettes import Category10
from bokeh.models import Div, Panel
from bokeh.layouts import column

# If you're in Jupyter
output_notebook()

# -----------------------------------
# 0. Define seniority columns (order matters)
# -----------------------------------
seniority_cols = [
    '110.Entry-Level',
    '120.Experienced',
    '130.Distinguished',
    '200.Entry-Level Manager',
    '210.Experienced Manager',
    '220.Director-Level',
    '300.Vice President-Level',
    '310.CXO-Level'
    # '320.Organizational Governance'
]

entry_col = '110.Entry-Level'
top_col   = '310.CXO-Level'


# -----------------------------------
# 1. Helper: build Bokeh figures for a given country df
# -----------------------------------
def make_country_figs(df_country, country_label):

    df_country = df_country.copy()

    # ---- Long format for full seniority curve ----
    df_long = df_country.melt(
        id_vars=['Sector'],
        value_vars=seniority_cols,
        var_name='Seniority_Level',
        value_name='Women_Share'
    )

    df_long['Seniority_Level'] = pd.Categorical(
        df_long['Seniority_Level'],
        categories=seniority_cols,
        ordered=True
    )

    sectors = df_long['Sector'].unique().tolist()
    n_sectors = len(sectors)
    palette = Category10[10] if n_sectors <= 10 else (Category10[10] * ((n_sectors // 10) + 1))
    
    # ---- Figure 1: one line per sector across all levels ----
    p1 = figure(
        x_range=seniority_cols,
        height=400,
        width=800,
        title=f"Women’s Share Across Seniority Levels by Sector ({country_label})",
        toolbar_location="above"
    )
    p1.xaxis.major_label_orientation = 0.8
    p1.xaxis.axis_label = "Seniority level"
    p1.yaxis.axis_label = "Women’s share"

    # Hover: only value, only on the point under the mouse
    hover1 = HoverTool(
        tooltips=[
            ("Women’s share", "@Women_Share{0.0}")
        ],
        mode="mouse"       # <--- key change: no more vline all-series hover
    )
    p1.add_tools(hover1)

    for i, sector in enumerate(sectors):
        d_sec = df_long[df_long['Sector'] == sector].sort_values('Seniority_Level')
        source = ColumnDataSource(d_sec)
        color = palette[i]

        p1.line(
            x='Seniority_Level',
            y='Women_Share',
            source=source,
            line_width=2,
            color=color,
            legend_label=sector
        )
        p1.scatter(
            x='Seniority_Level',
            y='Women_Share',
            source=source,
            size=6,
            color=color
        )

    p1.legend.location = "top_right"
    p1.legend.click_policy = "hide"

    # ---- Figure 2: slope chart entry -> CXO-Level ----
    df_slope = (
        df_country
        .loc[:, ['Sector', entry_col, top_col]]
        .melt(
            id_vars='Sector',
            value_vars=[entry_col, top_col],
            var_name='Seniority_Level',
            value_name='Women_Share'
        )
    )

    # nicer labels for x-axis
    level_label_map = {
        entry_col: "Entry level",
        top_col: "CXO-Level"
    }
    df_slope['Level_label'] = df_slope['Seniority_Level'].map(level_label_map)

    p2 = figure(
        x_range=["Entry level", "CXO-Level"],
        height=350,
        width=800,
        title=f"Drop in Women’s Representation: Entry Level → CXO-Level ({country_label})",
        toolbar_location="above"
    )
    p2.xaxis.axis_label = "Seniority level"
    p2.yaxis.axis_label = "Women’s share"

    hover2 = HoverTool(
        tooltips=[
            ("Women’s share", "@Women_Share{0.0}")
        ],
        mode="mouse"
    )
    p2.add_tools(hover2)

    for i, sector in enumerate(sectors):
        d_sec = df_slope[df_slope['Sector'] == sector].sort_values('Level_label')
        source = ColumnDataSource(d_sec)
        color = palette[i]

        p2.line(
            x='Level_label',
            y='Women_Share',
            source=source,
            line_width=2,
            color=color,
            legend_label=sector
        )
        p2.scatter(
            x='Level_label',
            y='Women_Share',
            source=source,
            size=6,
            color=color
        )

    p2.legend.location = "top_right"
    p2.legend.click_policy = "hide"

    layout_country = column(p1, p2)
    return layout_country


# -----------------------------------
# 2. Filter for each country using `seniority_name_display`
#    (adjust string matches if needed)
# -----------------------------------
df_gender_alg = df_gender[df_gender['seniority_name_display']
                          .str.contains("Algeria", case=False, na=False)]

df_gender_us = df_gender[df_gender['seniority_name_display']
                         .str.contains("United States", case=False, na=False)]



# -----------------------------------
# README 
# -----------------------------------

readme_text = """
<h3>Seniority Level Definitions</h3>

<p><strong>Individual Contributor (IC)</strong> roles refer to employees who <em>do not</em> manage others. 
They have no direct reports, although they may lead technical projects or workstreams.</p>

<ul>
<li><strong>Entry-Level (IC – 110):</strong> Early-career employees with limited experience.</li>
<li><strong>Experienced (IC – 120):</strong> Employees with established skills and experience.</li>
<li><strong>Distinguished (IC – 130):</strong> Senior technical experts without managerial duties.</li>
</ul>

<p><strong>Mid-Level Management</strong> includes employees who supervise one or more direct reports.</p>

<ul>
<li><strong>Entry-Level Manager (200):</strong> Leads a small team or supervises limited staff.</li>
<li><strong>Experienced Manager (210):</strong> Manages larger teams or multiple functional units.</li>
<li><strong>Director (220):</strong> Oversees significant departmental planning and execution.</li>
</ul>

<p><strong>Leadership</strong> roles hold strategic responsibility over major business functions 
or the entire organization.</p>

<ul>
<li><strong>Vice President-Level (300):</strong> Senior leaders managing major business units.</li>
<li><strong>C-Suite Executives (310):</strong> Top-level officers such as CEO, COO, CFO, CTO.</li>
</ul>

<hr>
<p><strong>Source:</strong> LinkedIn The State of Women in Leadership.</p>
"""

readme_div = Div(text=readme_text, width=800)
tab_readme = TabPanel(child=readme_div, title="README")


# -----------------------------------
# 3. Build tabs (one for Algeria, one for US)
# -----------------------------------

title_div = Div(
    text="<h2 style='text-align:center; margin-bottom:10px;'>Women’s Representation Across Leadership Levels</h2>"
)

alg_layout = make_country_figs(df_gender_alg, "Algeria")
us_layout  = make_country_figs(df_gender_us, "United States")

tab_alg = TabPanel(child=alg_layout, title="Algeria")
tab_us  = TabPanel(child=us_layout, title="United States")

# Add README tab
tabs = Tabs(tabs=[tab_alg, tab_us, tab_readme])

final_layout = column(title_div, tabs)

show(final_layout)

Loading BokehJS ...